In [1]:
import sys
sys.path.append('../library')
sys.path.append('../library/rtde')
import logging
import rtde.rtde as rtde
import rtde.rtde_config as rtde_config
import time
import math
import subprocess
import os
import ovr
from quaternion import quaternion
import keyboard

ovr.initialize(None)
session, luid = ovr.create()


In [2]:
#logging.basicConfig(level=logging.INFO)

ROBOT_HOST = '192.168.188.123'
ROBOT_PORT = 30004
config_filename = '../config/pose_pilot_configuration_with_button.xml'

keep_running = True
logging.getLogger().setLevel(logging.INFO)

In [3]:
conf = rtde_config.ConfigFile(config_filename)
state_names, state_types = conf.get_recipe('state')
setp_names, setp_types = conf.get_recipe('setp')
watchdog_names, watchdog_types = conf.get_recipe('watchdog')
button_names, button_types = conf.get_recipe('button')

In [4]:
con = rtde.RTDE(ROBOT_HOST, ROBOT_PORT)
con.connect()

# get controller version
con.get_controller_version()

# setup recipes
con.send_output_setup(state_names, state_types)
setp = con.send_input_setup(setp_names, setp_types)
watchdog = con.send_input_setup(watchdog_names, watchdog_types)
button = con.send_input_setup(button_names, button_types)

INFO:root:Controller version: 3.5.4.0


In [5]:
class deltaTransform:
    def __init__(self, original_base, scale, target_base):
        self.o_base = original_base
        self.scale = scale
        self.t_base = target_base
        
    def doTransform(self, original_point):
        # scale and original point delta
        scaled_point = [s*(o-b) for s, b , o in zip(self.scale, self.o_base, original_point)]
        # transform cartesians
        # TODO: make it general, this only works to swap y and z
        scaled_point[0], scaled_point[1], scaled_point[2] = -scaled_point[0], scaled_point[2], scaled_point[1]
        
        t_point = [t+s for t, s in zip(self.t_base, scaled_point)]
        return t_point

In [6]:
def setp_to_list(setp):
    list = []
    for i in range(0,6):
        list.append(setp.__dict__["input_double_register_%i" % i])
    return list

def list_to_setp(setp, list):
    for i in range (0,6):
        setp.__dict__["input_double_register_%i" % i] = list[i]
    return setp

def button_to_list(button):
    list = []
    for i in range(0,2):
        list.append(button.__dict__["input_int_register_%i" % (i+1)])
    return list

def list_to_button(button, list):
    for i in range (0,2):
        button.__dict__["input_int_register_%i" % (i+1)] = list[i]
    return button

In [7]:
# Initialization
# setp
setp.input_double_register_0 = 0
setp.input_double_register_1 = 0
setp.input_double_register_2 = 0
setp.input_double_register_3 = 0
setp.input_double_register_4 = 0
setp.input_double_register_5 = 0

# button
button.input_int_register_1 = 0
button.input_int_register_2 = 0
  
# The function "rtde_set_watchdog" in the "rtde_control_loop.urp" creates a 1 Hz watchdog
watchdog.input_int_register_0 = 0

# Orientation inputs (Controller Base Orientation + Robot Base Orientation + Cordinate rotation from controller to robot)

# # Input Controller Base Orientation
ts  = ovr.getTrackingState(session, ovr.getTimeInSeconds(), True)

# Input Robot Base Orientation
rob_base_ori_aangle = [math.pi/2,0,0]

# Input Coordinate rotation from controller to robot
cor_rot_aangle1 = [0,-math.pi,0]
cor_rot_aangle2 = [math.pi/2,0,0]
cor_rot1 = quaternion.axis_angle_to_quaternion(cor_rot_aangle1)
cor_rot2 = quaternion.axis_angle_to_quaternion(cor_rot_aangle2)
cor_rot = cor_rot2.multiply(cor_rot1)
#cor_rot = cor_rot2

# processing orientation inputs
Rtouch = ts.HandPoses[1]
a = Rtouch.ThePose.Position   
b = Rtouch.ThePose.Orientation
con_base_ori = quaternion(b[3],b[0],b[1],b[2])
rob_base_ori = quaternion.axis_angle_to_quaternion(rob_base_ori_aangle)

# location trnasformation 
rob_base_loc = [0.13, -0.61, 0.30] # communication to robot is in meters and radians
con_base_loc = [a[0], a[1], a[2]] # communication with controller is in mm and rad
scale = [1, 1, 1]
tr = deltaTransform(con_base_loc, scale, rob_base_loc)

In [8]:
#start data synchronization
if not con.send_start():
    sys.exit()

# control loop
while keep_running:
    # receive the current state
    state = con.receive()
    
    if state is None:
        break;
    
    # get new setp
    # Controller Current Orientation in Controller cordinates
    ts  = ovr.getTrackingState(session, ovr.getTimeInSeconds(), True)
    Rtouch = ts.HandPoses[1]
    con_loc = Rtouch.ThePose.Position
    con_ori = Rtouch.ThePose.Orientation
    con_ori = quaternion(con_ori[3], con_ori[0], con_ori[1], con_ori[2])
    
    # get delta in controller coordinates(rotation between current and base orientation of the controller)
    con_delta_rot = con_ori.delta(con_base_ori)
    con_delta_rot_aangle = con_delta_rot.to_axis_angle()
    
    # Get delta in robot coordinate
    delta_in_rob_cor_aangle = cor_rot.rotate_vector(con_delta_rot_aangle)
    delta_in_rob_cor = quaternion.axis_angle_to_quaternion(delta_in_rob_cor_aangle)
    
    # get current robot orientation
    rob_ori = delta_in_rob_cor.multiply(rob_base_ori)
    
    new_setp = tr.doTransform([con_loc[0], con_loc[1], con_loc[2]]) + list(rob_ori.to_axis_angle())
    list_to_setp(setp, new_setp)
    
    # send new setpoint        
    con.send(setp)
    
    # Get button data
    new_button = [0, 0]
    if keyboard.is_pressed('c'):
            new_button[0] = 1
    if keyboard.is_pressed('o'):
            new_button[1] = 1
    print(new_button)
    list_to_button(button, new_button)
    
    # Send button data
    con.send(button)
    
    # kick watchdog
    con.send(watchdog)

INFO:root:RTDE synchronization started
INFO:root:skipping package(1)
INFO:root:skipping package(1)
INFO:root:skipping package(1)
INFO:root:skipping package(1)
INFO:root:skipping package(1)
INFO:root:skipping package(1)
INFO:root:skipping package(1)
INFO:root:skipping package(1)
INFO:root:skipping package(1)
INFO:root:skipping package(1)
INFO:root:skipping package(1)
INFO:root:skipping package(1)
INFO:root:skipping package(1)
INFO:root:skipping package(1)
INFO:root:skipping package(1)
INFO:root:skipping package(1)
INFO:root:skipping package(1)
INFO:root:skipping package(1)
INFO:root:skipping package(1)
INFO:root:skipping package(1)
INFO:root:skipping package(1)
INFO:root:skipping package(1)
INFO:root:skipping package(1)
INFO:root:skipping package(1)
INFO:root:skipping package(1)
INFO:root:skipping package(1)
INFO:root:skipping package(1)
INFO:root:skipping package(1)
INFO:root:skipping package(1)
INFO:root:skipping package(1)
INFO:root:skipping package(1)
INFO:root:skipping package(1)
I

[0, 0]


INFO:root:skipping package(1)
INFO:root:skipping package(1)
INFO:root:skipping package(1)
INFO:root:skipping package(1)
INFO:root:skipping package(1)
INFO:root:skipping package(1)
INFO:root:skipping package(1)
INFO:root:skipping package(1)
INFO:root:skipping package(1)
INFO:root:skipping package(1)
INFO:root:skipping package(1)
INFO:root:skipping package(1)
INFO:root:skipping package(1)
INFO:root:skipping package(1)
INFO:root:skipping package(1)
INFO:root:skipping package(1)
INFO:root:skipping package(1)
INFO:root:skipping package(1)
INFO:root:skipping package(1)
INFO:root:skipping package(1)
INFO:root:skipping package(1)
INFO:root:skipping package(1)
INFO:root:skipping package(1)
INFO:root:skipping package(1)
INFO:root:skipping package(1)
INFO:root:skipping package(1)
INFO:root:skipping package(1)
INFO:root:skipping package(1)
INFO:root:skipping package(1)
INFO:root:skipping package(1)
INFO:root:skipping package(1)
INFO:root:skipping package(1)
INFO:root:skipping package(1)
INFO:root:

[0, 0]
[0, 0]
[0, 0]
[0, 0]


INFO:root:skipping package(1)
INFO:root:skipping package(1)
INFO:root:skipping package(1)
INFO:root:skipping package(1)
INFO:root:skipping package(1)
INFO:root:skipping package(1)
INFO:root:skipping package(1)
INFO:root:skipping package(1)
INFO:root:skipping package(1)
INFO:root:skipping package(1)


...

[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]

INFO:root:skipping package(1)


[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]

[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]
[0, 0]


error: [Errno 10054] An existing connection was forcibly closed by the remote host

In [ ]:
con.send_pause()
con.disconnect()
sys.stdout.flush()
ovr.destroy(session)
ovr.shutdown()

In [ ]:
sys.stdout.flush()
ovr.destroy(session)
ovr.shutdown()